In [41]:
import json
import os
import time
import requests
from fastprogress.fastprogress import master_bar, progress_bar

def get_sols(problem_code_id):
    status = "Success"
    auth_header = {
    # Replace this with your own auth header from the platform
    }
    target_year = 2020
    cur_year = 2023
    cur_page = 0
    max_pages = 0
    min_pages = 0
    data = []
    test_last_page = False
    while cur_year != target_year:
        sol_correct = f"https://www.codechef.com/api/submissions/PRACTICE/{problem_code_id}?limit=20&page={cur_page}&language=PYTH%25203&status=Correct&usernames="
        response = requests.get(sol_correct, headers=auth_header)
        if not "data" in response.json():
            if response.json()["message"] == "Invalid Language!":
                return {"status":"NoPythonSol", "data":[]}
            print(response.json())
        data=response.json()['data']
        if len(data) == 0:
            return {"status":"NoPythonSol", "data":[]}
        epoch_time = data[0]['submission_date']
        cur_year = time.localtime(epoch_time).tm_year
        # binary search for a better page number that might have the required year
        if not test_last_page:
            test_last_page = True
            max_pages = int(response.json()["count"]) // 20 - 1
            sol_last = f"https://www.codechef.com/api/submissions/PRACTICE/{problem_code_id}?limit=20&page={max_pages}&language=PYTH%25203&status=Correct&usernames="
            response_last = requests.get(sol_last, headers=auth_header)
            data_last=response_last.json()['data']
            epoch_last = data_last[0]['submission_date']
            last_year = time.localtime(epoch_last).tm_year
            if last_year >= target_year:
                status = f"Last-{last_year}"
                # data = None
                break
        if max_pages == min_pages:
            break
        if cur_year > target_year:
            # go to one of the next pages that might have the required year and update min_pages
            min_pages = cur_page + 1
            new_page = (min_pages + max_pages) // 2
        else:
            # go to one of the previous pages that might have the required year and update max_pages
            max_pages = cur_page - 1
            new_page = (min_pages + max_pages) // 2
        if new_page == cur_page:
            break
        else:
            cur_page = new_page
        time.sleep(1)
    # drop items from data (a list of objects) that have same username
    usernames = set()
    useful_data = []

    if data is None:
        return None
    for i in range(len(data)):
        if data[i]['username'] in usernames:
            continue
        else:
            usernames.add(data[i]['username'])
            useful_data.append(data[i])
    if len(useful_data) > 5:
        useful_data = useful_data[:5]
    for i in range(len(useful_data)):
        useful_data[i]['code'] = requests.get(f"https://www.codechef.com/api/submission-code/{useful_data[i]['id']}", headers=auth_header).json()['data']['code']
    useful_data = {"status":status, "data":useful_data}
    return useful_data

with open("human_solved.json", "r") as f:
    cleaned_data = json.load(f)
modified_data = cleaned_data.copy()
mb = master_bar(cleaned_data.items())
for level, problems in mb:
    for key, problem_data in progress_bar(problems.items(), parent=mb):
        if "human_solutions" in problem_data:
            # print("Skipped", key, "as it already has human solutions")
            continue
        else:
            time.sleep(1)
            solutions_fetched = get_sols(problem_data["problem_code_id"])
            if solutions_fetched is None:
                print("No solutions found for", key)
                solutions_fetched = []
            modified_data[level][key]["human_solutions"] = solutions_fetched
        # print("Processing", index+1, "out of", len(problems))
        with open("human_solved.json", "w") as f:
            json.dump(modified_data, f)

In [53]:
with open("human_solved.json", "r") as f:
    final_data = json.load(f)
distribution = []
stat_distribution = []
perfect_sols = []
for level, problems in cleaned_data.items():
    for key, problem_data in problems.items():
        distribution.append(len(problem_data["human_solutions"]["data"]))
        stat_distribution.append(problem_data["human_solutions"]["status"])
        if len(problem_data["human_solutions"]["data"]) >= 2:
            if problem_data["human_solutions"]["status"] in ("Success", "Last-2020"):
                perfect_sols.append(level)

In [47]:
# summarize distribution frequency
from collections import Counter
counter = Counter(distribution)
for k,v in counter.items():
    per = v / len(distribution) * 100
    print('Class=%d, n=%d (%.3f%%)' % (k, v, per))

Class=5, n=787 (71.545%)
Class=0, n=253 (23.000%)
Class=4, n=13 (1.182%)
Class=3, n=12 (1.091%)
Class=1, n=24 (2.182%)
Class=2, n=11 (1.000%)


In [50]:
from collections import Counter
counter = Counter(stat_distribution)
for k,v in counter.items():
    per = v / len(stat_distribution) * 100
    print('Class=%s, n=%d (%.3f%%)' % (k, v, per))

Class=Success, n=368 (33.455%)
Class=Last-2021, n=68 (6.182%)
Class=Last-2020, n=35 (3.182%)
Class=Last-2023, n=202 (18.364%)
Class=Last-2022, n=174 (15.818%)
Class=NoPythonSol, n=253 (23.000%)


In [54]:
len(perfect_sols)

391

In [55]:
from collections import Counter
counter = Counter(perfect_sols)
for k,v in counter.items():
    per = v / len(perfect_sols) * 100
    print('Class=%s, n=%d (%.3f%%)' % (k, v, per))

Class=0, n=13 (3.325%)
Class=1, n=45 (11.509%)
Class=1*, n=71 (18.159%)
Class=2, n=55 (14.066%)
Class=2*, n=56 (14.322%)
Class=3, n=57 (14.578%)
Class=3*, n=50 (12.788%)
Class=4, n=31 (7.928%)
Class=5, n=8 (2.046%)
Class=6, n=4 (1.023%)
Class=7, n=1 (0.256%)
